# Driving over a Speed Bump

*MES Advanced Vehicle Dynamics* Project

In [1]:
import numpy as np
import pandas as pd
from io import StringIO
import matplotlib.pyplot as plt
from pathlib import Path
from itertools import product
from tqdm.auto import tqdm, trange
import plotly.express as px
from scipy import signal

test_path = Path('./AVD2324')

In [2]:
assert test_path.is_dir()

os.stat_result(st_mode=16895, st_ino=562949953806924, st_dev=2763055692, st_nlink=1, st_uid=0, st_gid=0, st_size=4096, st_atime=1697325626, st_mtime=1696855229, st_ctime=1696855227)

In [3]:
# Our different tests organized by speed
tests = [
    (10, [1,2,3]),
    (15, [4,5,6]),
    (20, [7,8,9]),
    (25, [10,11,12]),
    (40, [13,14,15]),
]

In [5]:
def load_vibration_data(n):
        # Charger les données en sautant la première et la troisième lignes
        return pd.read_csv(test_path / f"Vibration Data_{n}.txt", delimiter="\t", skiprows=[0, 2], header=0)

In [6]:
df1 = load_vibration_data(1)
df1

Time  Vehicle Speed  FL Sprung acceleration  FR Sprung acceleration  \
0       0.000          9.341                  -0.057                  -0.024   
1       0.000          9.341                  -0.060                  -0.025   
2       0.000          9.348                  -0.064                  -0.024   
3       0.001          9.338                  -0.069                  -0.023   
4       0.001          9.335                  -0.073                  -0.020   
...       ...            ...                     ...                     ...   
68095  13.619          7.471                  -0.004                  -0.057   
68096  13.619          7.486                  -0.006                  -0.058   
68097  13.619          7.498                  -0.006                  -0.060   
68098  13.620          7.486                  -0.007                  -0.061   
68099  13.620          7.498                  -0.006                  -0.062   

       RL Sprung acceleration  RR Sprung acceleration  \
0                      -0.080                   0.184   
1                      -0.100                   0.148   
2                      -0.115                   0.112   
3                      -0.128                   0.077   
4                      -0.135                   0.043   
...                       ...                     ...   
68095                  -0.096                  -0.167   
68096                  -0.097                  -0.158   
68097                  -0.097                  -0.147   
68098                  -0.095                  -0.132   
68099                  -0.093                  -0.116   

       FL Unsprung acceleration  FR Unsprung acceleration  \
0                         0.875                     0.570   
1                         0.875                     0.559   
2                         0.871                     0.546   
3                         0.862                     0.548   
4                         0.847                     0.544   
...                         ...                       ...   
68095                     0.570                     0.726   
68096                     0.556                     0.746   
68097                     0.558                     0.726   
68098                     0.566                     0.705   
68099                     0.550                     0.698   

       RL Unsprung acceleration  RR Unsprung acceleration  Bellow pressure RL  \
0                         0.478                     1.380               1.851   
1                         0.439                     1.396               1.844   
2                         0.429                     1.392               1.841   
3                         0.488                     1.418               1.844   
4                         0.547                     1.445               1.852   
...                         ...                       ...                 ...   
68095                     0.460                     0.910               1.854   
68096                     0.458                     0.901               1.843   
68097                     0.463                     0.889               1.845   
68098                     0.456                     0.869               1.841   
68099                     0.480                     0.894               1.847   

       Bellow pressure RR  Acceleration X  Acceleration Y  Acceleration Z  
0                   1.822          -0.048           0.050          -0.033  
1                   1.820          -0.047           0.047          -0.032  
2                   1.824          -0.046           0.043          -0.031  
3                   1.824          -0.044           0.042          -0.031  
4                   1.819          -0.041           0.038          -0.029  
...                   ...             ...             ...             ...  
68095               1.745          -0.060           0.061          -0.125  
68096               1.751          -0.060        

In [7]:
px.line(df1, x="Time", y=["FL Sprung acceleration", "FL Unsprung acceleration"])

## Filters

Here we define easy to use highpass/lowpass filters. (wrappers around scipy methods)

In [8]:
def lowpass(data: np.ndarray, cutoff: float, sample_rate: float, poles: int = 5):
    sos = signal.butter(poles, cutoff, 'lowpass', fs=sample_rate, output='sos')
    filtered_data = signal.sosfiltfilt(sos, data)
    return filtered_data


def highpass(data: np.ndarray, cutoff: float, sample_rate: float, poles: int = 5):
    sos = signal.butter(poles, cutoff, 'highpass', fs=sample_rate, output='sos')
    filtered_data = signal.sosfiltfilt(sos, data)
    return filtered_data


## Speed and Position Calculation

Deduce Speed then Postition from the measured accelerations on the sensors

In [28]:
locations = ["FL", "FR", "RL", "RR"]

types = ["Sprung", "Unsprung"]

def compute_tires_speed_pos(df, bump_time=9.45,  highpass_cutoff=0.5, lowpass_cutoff=18):
    time_step = df["Time"].diff().mean()
    
    for loc, type in product(locations, types):
        acceleration_fixed = df[f"{loc} {type} acceleration"] - df[f"{loc} {type} acceleration"][df["Time"] < bump_time].mean()
        acceleration_fixed = lowpass(acceleration_fixed.to_numpy(), lowpass_cutoff, 1/time_step) * 9.81
        acceleration_fixed = highpass(acceleration_fixed, highpass_cutoff, 1/time_step)
        df[f"{loc} {type} acceleration fixed"] = acceleration_fixed
        
    # df = df[df["Time"] >= bump_time]
    
    augmentations = [
        ("acceleration fixed", "speed"),
        ("speed", "position"),
    ]
    
    for loc, type, (base, integrated) in product(locations, types, augmentations):
        # value = 0
        
        # def integrate(x):
        #     nonlocal value
        #     value += time_step * x
        #     return value
        
        # Integrate using the rectangular method
        res = df[f"{loc} {type} {base}"].cumsum() * time_step
        
        # if integrated == "speed":
            # df[f"{loc} {type} {integrated}"] = df[f"{loc} {type} {integrated}"] - df[f"{loc} {type} {integrated}"][df["Time"] < bump_time].mean()
            
        # Filter using the potential shift intruduced by the noise of the sensor
        res = highpass(res, highpass_cutoff, 1/time_step)
            
        df[f"{loc} {type} {integrated}"] = res
        
    return df
        
    
    

In [10]:
compute_tires_speed_pos(df1)

Time  Vehicle Speed  FL Sprung acceleration  FR Sprung acceleration  \
0       0.000          9.341                  -0.057                  -0.024   
1       0.000          9.341                  -0.060                  -0.025   
2       0.000          9.348                  -0.064                  -0.024   
3       0.001          9.338                  -0.069                  -0.023   
4       0.001          9.335                  -0.073                  -0.020   
...       ...            ...                     ...                     ...   
68095  13.619          7.471                  -0.004                  -0.057   
68096  13.619          7.486                  -0.006                  -0.058   
68097  13.619          7.498                  -0.006                  -0.060   
68098  13.620          7.486                  -0.007                  -0.061   
68099  13.620          7.498                  -0.006                  -0.062   

       RL Sprung acceleration  RR Sprung acceleration  \
0                      -0.080                   0.184   
1                      -0.100                   0.148   
2                      -0.115                   0.112   
3                      -0.128                   0.077   
4                      -0.135                   0.043   
...                       ...                     ...   
68095                  -0.096                  -0.167   
68096                  -0.097                  -0.158   
68097                  -0.097                  -0.147   
68098                  -0.095                  -0.132   
68099                  -0.093                  -0.116   

       FL Unsprung acceleration  FR Unsprung acceleration  \
0                         0.875                     0.570   
1                         0.875                     0.559   
2                         0.871                     0.546   
3                         0.862                     0.548   
4                         0.847                     0.544   
...                         ...                       ...   
68095                     0.570                     0.726   
68096                     0.556                     0.746   
68097                     0.558                     0.726   
68098                     0.566                     0.705   
68099                     0.550                     0.698   

       RL Unsprung acceleration  RR Unsprung acceleration  ...  \
0                         0.478                     1.380  ...   
1                         0.439                     1.396  ...   
2                         0.429                     1.392  ...   
3                         0.488                     1.418  ...   
4                         0.547                     1.445  ...   
...                         ...                       ...  ...   
68095                     0.460                     0.910  ...   
68096                     0.458                     0.901  ...   
68097                     0.463                     0.889  ...   
68098                     0.456                     0.869  ...   
68099                     0.480                     0.894  ...   

       FR Unsprung speed  FR Unsprung position  RL Sprung speed  \
0              -0.014199             -0.000443        -0.018438   
1              -0.014132             -0.000447        -0.018563   
2              -0.014065             -0.000450        -0.018686   
3              -0.014000             -0.000453        -0.018808   
4              -0.013937             -0.000456        -0.018928   
...                  ...                   ...              ...   
68095           0.001025              0.000025         0.001021   
68096           0.000977              0.000024         0.000974   
68097           0.000930              0.000023         0.000928   
68098           0.000883              0.000022         0.000882   
68099           0.000836              0.000021         0.000835   

       RL Sprung position  RL Un

Convenience method for ploting time data from the main dataframe we work with

In [23]:
def plot_data(df, data="position", location="FL", sample_step=100, bump_time=None, **kwargs):
    df = df.iloc[::sample_step, :]
    if bump_time is not None:
        df = df[df["Time"] > bump_time]
    return px.line(df, x="Time", y=[f"{location} Sprung {data}", f"{location} Unsprung {data}"], **kwargs)

In [12]:
Ms = {
    "FR": 660,
    "FL": 782,
    "RR": 684,
    "RL": 694,
}

ks = lambda f, m: m * (2*np.pi / f) ** 2

freqs = {
    2: {
        "FL": 1.341,
        "FR": 1.877,
        "RL": 2.372,
        "RR": 2.372,
    }
}

In [13]:
df2 = load_vibration_data(2)
plot_data(df2, data="acceleration")

In [14]:
df2 = compute_tires_speed_pos(df2, bump_time=6.2)
plot_data(df2)

In [15]:
plot_data(df2, data="speed")

In [16]:
plot_data(df2, data="acceleration fixed")

In [17]:
plot_data(df2, data="acceleration fixed")

In [19]:
T = df2.Time.diff().mean()
T

0.00020000327069943908

In [20]:
1/T

4999.9182338511855

In [21]:
# Assumons que acc_data est votre données d'accélération
f, Pxx = signal.welch(df2["FL Sprung acceleration"], fs=1/T, nperseg=16384)

px.line(x=f, y=Pxx, log_y=True, labels=dict(x='Frequency [Hz]', y='PSD [V**2/Hz]')).show()

idx = np.argmax(Pxx)
print("Fondammental", f[idx])

Fondammental 2.136195534482318


# The Graphs

In [29]:
for test_speed, test_data in tests:
    print(f"# V = {test_speed} km/h")
    for test in test_data:
        print(f"## Test {test}")
        
        df = load_vibration_data(test)
        
        # px.line(df, x="Time", y="FL Sprung acceleration", title="(raw data to measure bump time)").show()
        
        bump_peak_idx = df["FL Sprung acceleration"].idxmax()
        
        # bump_time = float(input("Bump time (s) = "))
        bump_time = df["Time"][bump_peak_idx] - 0.5
        print("estimated bump time:", bump_time)

        compute_tires_speed_pos(df, bump_time=bump_time, lowpass_cutoff=25)
        
        print("Graphs:")

        for pos in ['FL', 'FR', 'RL', 'RR']:
            plot_data(df, location=pos, bump_time=bump_time, title=f"{pos} tire position at {test_speed} km/h (Test {test})").show()

# V = 10 km/h
## Test 1
estimated bump time: 9.109
Graphs:


## Test 2
estimated bump time: 8.299
Graphs:


## Test 3
estimated bump time: 7.853999999999999
Graphs:


# V = 15 km/h
## Test 4
estimated bump time: 7.123
Graphs:


## Test 5
estimated bump time: 5.824
Graphs:


...

## Test 11
estimated bump time: 3.7089999999999996
Graphs:


## Test 12
estimated bump time: 2.274
Graphs:


# V = 40 km/h
## Test 13
estimated bump time: 1.368
Graphs:


## Test 14
estimated bump time: 1.246
Graphs:


## Test 15
estimated bump time: 0.16800000000000004
Graphs:
